# Importing libraries and datasets

In [1]:
import time
start = time.time()

In [2]:
# Importing the libraries
import pandas as pd
import numpy as np

In [3]:
# Importing training datasets
#df = pd.read_csv('train_transaction.csv')
df_tr = pd.read_csv('train_transaction.csv')
df_id = pd.read_csv('train_identity.csv')

In [4]:
df = pd.merge(df_tr, df_id, how='left')
df.shape

(590582, 434)

In [5]:
# Importing testing datasets
#df_test = pd.read_csv('test_transaction.csv')
df_test_tr = pd.read_csv('test_transaction.csv')
df_test_id = pd.read_csv('test_identity.csv')

In [6]:
df_test = pd.merge(df_test_tr, df_test_id, how='left')
df_test.shape

(506691, 433)

In [7]:
# Dropping column 'DeviceInfo'
df.drop(['id_33','DeviceInfo'], axis=1, inplace=True)
df_test.drop(['id_33','DeviceInfo'], axis=1, inplace=True)

# Data cleansing part

In [8]:
# Making the clone of df
df_corr_cleanse = df.copy()

In [9]:
# Getting list of categorical columns
categorical_cols = df.columns.groupby(df.dtypes == 'object')[1]

In [10]:
# Taking care of categorical data for correlation estimation
from sklearn.preprocessing import LabelEncoder
labelencoder_X = LabelEncoder()
df_corr_cleanse[categorical_cols] = df_corr_cleanse[categorical_cols].apply(lambda col: labelencoder_X.fit_transform(col.astype(str)))

In [11]:
df_corr_cleanse.shape

(590582, 432)

In [12]:
# Columns with correlation to 'isFraud' <= 0.01
#corr_list_drop = df_corr_cleanse.columns[1:][abs(df_corr_cleanse[df_corr_cleanse.columns[1:]].corr()['isFraud']) <= 0.01]

In [13]:
# Dropping columns in training set
#df.drop(corr_list_drop, axis=1, inplace=True)
df.shape

(590582, 432)

In [14]:
pd.options.display.max_columns=400
pd.options.display.max_rows=400
df.head(12).transpose()

0        1        2        3        4        5        6   \
TransactionID   2987000  2987001  2987002  2987003  2987004  2987005  2987006   
isFraud               0        0        0        0        0        0        0   
TransactionDT     86400    86401    86469    86499    86506    86510    86522   
TransactionAmt     68.5       29       59       50       50       49      159   
ProductCD             W        W        W        W        H        W        W   
...                 ...      ...      ...      ...      ...      ...      ...   
id_35               NaN      NaN      NaN      NaN        T      NaN      NaN   
id_36               NaN      NaN      NaN      NaN        F      NaN      NaN   
id_37               NaN      NaN      NaN      NaN        T      NaN      NaN   
id_38               NaN      NaN      NaN      NaN        T      NaN      NaN   
DeviceType          NaN      NaN      NaN      NaN   mobile      NaN      NaN   

                     7        8        9        10       11  
TransactionID   2987007  2987008  2987009  2987010  2987011  
isFraud               0        0        0        0        0  
TransactionDT     86529    86535    86536    86549    86555  
TransactionAmt    422.5       15      117   75.887   16.495  
ProductCD             W        H        W        C        C  
...                 ...      ...      ...      ...      ...  
id_35               NaN        T      NaN        F        F  
id_36               NaN        F      NaN        F        F  
id_37               NaN        F      NaN        T        T  
id_38               NaN        T      NaN        T        T  
DeviceType          NaN   mobile      NaN  desktop  desktop  

[432 rows x 12 columns]

In [15]:
# Dropping columns in test set
#df_test.drop(corr_list_drop, axis=1, inplace=True)
df_test.shape

(506691, 431)

In [16]:
# Getting the list if correlations with column 'isFraud'
#corr_list = df[df.columns[1:]].corr()['isFraud'][:].sort_values(ascending=False)

In [17]:
## Getting the list if no-correlation columns with column 'isFraud'
"""
import math
corr_list_drop = []
for i in range (corr_list.shape[0]):
    if math.isnan(corr_list.values[i]):
        corr_list_drop.append(corr_list.index[i])      
"""      

'\nimport math\ncorr_list_drop = []\nfor i in range (corr_list.shape[0]):\n    if math.isnan(corr_list.values[i]):\n        corr_list_drop.append(corr_list.index[i])      \n'

In [18]:
# Dropping no-correlation columns with column 'isFraud'
#df.drop(corr_list_drop, axis=1, inplace=True)
df.shape

(590582, 432)

In [19]:
# Dropping no-correlation columns with column 'isFraud'
#df_test.drop(corr_list_drop, axis=1, inplace=True)
df_test.shape

(506691, 431)

In [20]:
empty_columns_drop = df.columns[df.isna().sum() == df.shape[0]]

In [21]:
# Dropping empty columns
df.drop(empty_columns_drop, axis=1, inplace=True)
df.shape

(590582, 432)

In [22]:
# Dropping empty columns
df_test.drop(empty_columns_drop, axis=1, inplace=True)
df_test.shape

(506691, 431)

# Data Preprocessing part

In [23]:
# Filling NaNs with 0
df.fillna(0, inplace=True)
df_test.fillna(0, inplace=True)

In [24]:
# Taking care of categorical values  
from sklearn.preprocessing import LabelEncoder
for i in range(0, len(categorical_cols)):
    labelencoder_X = LabelEncoder()
    df[categorical_cols[i]] = labelencoder_X.fit_transform(df[categorical_cols[i]].astype(str))
    df_test[categorical_cols[i]] = labelencoder_X.transform(df_test[categorical_cols[i]].astype(str))
    del labelencoder_X

In [25]:
isfraud_corr = df.corr()['isFraud']

In [26]:
isfraud_corr

TransactionID     0.013898
isFraud           1.000000
TransactionDT     0.013077
TransactionAmt    0.011311
ProductCD        -0.156562
                    ...   
id_35             0.092095
id_36             0.126164
id_37             0.136232
id_38             0.108381
DeviceType        0.143760
Name: isFraud, Length: 432, dtype: float64

In [27]:
# Correlation estimation and 
df_corr = pd.DataFrame(np.zeros((df.shape[1], 3)))
df_corr.columns = ['Field_name', 'Corr', 'Isna']

In [28]:
for i in range(0, df.shape[1]):
    df_corr['Field_name'][i] = df.columns[i]
    df_corr['Corr'][i] = isfraud_corr[i]
    df_corr['Isna'][i] = df.isna().sum()[i]

D:\Anaconda\lib\site-packages\ipykernel_launcher.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  This is separate from the ipykernel package so we can avoid doing imports until
D:\Anaconda\lib\site-packages\ipykernel_launcher.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  after removing the cwd from sys.path.
D:\Anaconda\lib\site-packages\ipykernel_launcher.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  


In [29]:
pd.options.display.max_columns=400
pd.options.display.max_rows=400
df.transpose()

0          1          2          3          4       \
TransactionID   2987000.0  2987001.0  2987002.0  2987003.0  2987004.0   
isFraud               0.0        0.0        0.0        0.0        0.0   
TransactionDT     86400.0    86401.0    86469.0    86499.0    86506.0   
TransactionAmt       68.5       29.0       59.0       50.0       50.0   
ProductCD             4.0        4.0        4.0        4.0        1.0   
...                   ...        ...        ...        ...        ...   
id_35                 0.0        0.0        0.0        0.0        2.0   
id_36                 0.0        0.0        0.0        0.0        1.0   
id_37                 0.0        0.0        0.0        0.0        2.0   
id_38                 0.0        0.0        0.0        0.0        2.0   
DeviceType            0.0        0.0        0.0        0.0        2.0   

                   5          6          7          8          9       \
TransactionID   2987005.0  2987006.0  2987007.0  2987008.0  2987009.0   
isFraud               0.0        0.0        0.0        0.0        0.0   
TransactionDT     86510.0    86522.0    86529.0    86535.0    86536.0   
TransactionAmt       49.0      159.0      422.5       15.0      117.0   
ProductCD             4.0        4.0        4.0        1.0        4.0   
...                   ...        ...        ...        ...        ...   
id_35                 0.0        0.0        0.0        2.0        0.0   
id_36                 0.0        0.0        0.0        1.0        0.0   
id_37                 0.0        0.0        0.0        1.0        0.0   
id_38                 0.0        0.0        0.0        2.0        0.0   
DeviceType            0.0        0.0        0.0        2.0        0.0   

                     10           11         12         13         14      \
TransactionID   2987010.000  2987011.000  2987012.0  2987013.0  2987014.0   
isFraud               0.000        0.000        0.0        0.0        0.0   
TransactionDT     86549.000    86555.000    86564.0    86585.0    86596.0   
TransactionAmt       75.887       16.495       50.0       40.0       10.5   
ProductCD             0.000        0.000        4.0        4.0        4.0   
...                     ...          ...        ...        ...        ...   
id_35                 1.000        1.000        0.0        0.0        0.0   
id_36                 1.000        1.000        0.0        0.0        0.0   
id_37                 2.000        2.000        0.0        0.0        0.0   
id_38                 2.000        2.000        0.0        0.0        0.0   
DeviceType            1.000        1.000        0.0        0.0        0.0   

                    15         16         17          18         19      \
TransactionID   2987015.00  2987016.0  2987017.0  2987018.00  2987019.0   
isFraud               0.00        0.0        0.0        0.00        0.0   
TransactionDT     86618.00    86620.0    86668.0    86725.00    86730.0   
TransactionAmt       57.95       30.0      100.0       47.95      186.0   
ProductCD             4.00        1.0        1.0        4.00        4.0   
...                    ...        ...        ...         ...        ...   
id_35                 0.00        2.0        2.0        0.00        0.0   
id_36                 0.00        1.0        1.0        0.00        0.0   
id_37                 0.00        2.0        2.0        0.00        0.0   
id_38                 0.00        2.0        2.0        0.00        0.0   
DeviceType            0.00        1.0        1.0        0.00        0.0   

                   20          21         22          23          24      \
TransactionID   2987020.0  2987021.00  2987022.0  2987023.00  2987024.00   
isFraud               0.0        0.00        0.0        0.00        0.00   
TransactionDT     86761.0    86769.00    86786.0    86808.00    86821.00   
TransactionAmt       39.0      159.95       50.0      107.95       73.95   
ProductCD             4.0        4.00        1.0        4.0

In [30]:
# Defining DV and IV
X = df.drop(['isFraud'], axis=1)
y = df['isFraud']

In [31]:
# Data scaling
from sklearn.preprocessing import StandardScaler
sc_X = StandardScaler()
X = sc_X.fit_transform(X)
X_test = sc_X.transform(df_test)

In [32]:
# Splitting the dataset into the Training set and Test set
X_train = X.copy()
y_train = y.copy()

# Building model

In [33]:
# Importing lightGBM
import lightgbm

parameters = {
    'application': 'binary',
    'objective': 'binary',
    'min_child_weight': 0.05,
    'max_depth': -1,
    'metric': 'auc',
    'is_unbalance': 'false',
    'boosting': 'gbdt',
    'num_leaves': 50,
    'feature_fraction': 0.5,
    'bagging_fraction': 0.5,
    'bagging_freq': 20,
    'learning_rate': 0.05,
    'verbose': 1
}

In [34]:
# Training and testing data preparation
train_data = lightgbm.Dataset(X_train, label = y_train)

In [35]:
# Model training
model = lightgbm.train(parameters,
                       train_data,
                       num_boost_round=5000)

In [36]:
y_pred = model.predict(X_test)

In [37]:
y_ind = pd.DataFrame(df_test['TransactionID'], index=None)
y_pred = round(pd.DataFrame(y_pred),1)
y_ind = pd.DataFrame(y_ind)
result = pd.concat([y_ind, y_pred], axis=1)
result.columns = ['TransactionID','isFraud']
result.set_index(['TransactionID'], inplace=True)
result.head(10)

isFraud
TransactionID         
3663549            0.0
3663550            0.0
3663551            0.0
3663552            0.0
3663553            0.0
3663554            0.0
3663555            0.0
3663556            0.0
3663557            0.0
3663558            0.0

In [38]:
# Writing to CSV file
result.to_csv(r'submission.csv')

In [39]:
end = time.time()
print(round(end - start,0), ' seconds')
print('OR')
print(round((end - start)/60,1), ' minutes')
print('OR')
print(round((end - start)/60/60,2), ' hours')

1388.0  seconds
OR
23.1  minutes
OR
0.39  hours


In [40]:
import winsound
winsound.PlaySound("SystemHand", winsound.SND_ALIAS)